# Exploração dos Dados

Vamos dividir nosso notebook em algumas etapas.
A primeira delas vai ser a de importação das bibliotecas que vamos utilizar.

# Importação das Bibliotecas

In [4]:
# Adição das bibliotecas faltantes
!python3 -m pip install yellowbrick
!python3 -m pip install ydata-profiling

  Obtaining dependency information for ydata-profiling from https://files.pythonhosted.org/packages/09/98/5a5fbfd48bf23acd3ceed5114d073b877965816304078151fefbf86d8458/ydata_profiling-4.5.1-py2.py3-none-any.whl.metadata
  Obtaining dependency information for pydantic<2,>=1.8.1 from https://files.pythonhosted.org/packages/b8/ae/8c3ffe3dafeaeb0fa08d6622e7fb074c7f42921fe8916c8de6f47662f9a4/pydantic-1.10.12-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.3/149.3 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.7/102.7 kB 7.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.1/17.1 MB 6.1 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 679.5/679.5 kB 9.9 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 3.0 MB/s eta 0:00:00a 0:00:01
  Obtaining dependency information for wordcloud>=1.9

In [3]:
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import(
    ensemble,
    preprocessing,
    tree,
)
from sklearn.metrics import(
    auc,
    confusion_matrix,
    roc_auc_score,
    roc_curve,
)
from sklearn.model_selection import (
    train_test_split,
    StratifiedKFold,
)
from yellowbrick.classifier import(
    ConfusionMatrix,
    ROCAUC,
)
from yellowbrick.model_selection import (
    LearningCurve,
)

# Carregando os dados

In [28]:
# Essa célula pode ser utilizada depois dos dados estarem consolidados
# URL para pegar os dados
url = (
    "./datasets/vgsales/vgsales.csv"
)
# Realiza o download dos dados
df = pd.read_csv(url)
# Faz uma cópia dos dados originais
orig_df = df

In [7]:
df

Rank                                              Name Platform  \
0          1                                        Wii Sports      Wii   
1          2                                 Super Mario Bros.      NES   
2          3                                    Mario Kart Wii      Wii   
3          4                                 Wii Sports Resort      Wii   
4          5                          Pokemon Red/Pokemon Blue       GB   
...      ...                                               ...      ...   
16593  16596                Woody Woodpecker in Crazy Castle 5      GBA   
16594  16597                     Men in Black II: Alien Escape       GC   
16595  16598  SCORE International Baja 1000: The Official Game      PS2   
16596  16599                                        Know How 2       DS   
16597  16600                                  Spirits & Spells      GBA   

         Year         Genre   Publisher  NA_Sales  EU_Sales  JP_Sales  \
0      2006.0        Sports    Nintendo     41.49     29.02      3.77   
1      1985.0      Platform    Nintendo     29.08      3.58      6.81   
2      2008.0        Racing    Nintendo     15.85     12.88      3.79   
3      2009.0        Sports    Nintendo     15.75     11.01      3.28   
4      1996.0  Role-Playing    Nintendo     11.27      8.89     10.22   
...       ...           ...         ...       ...       ...       ...   
16593  2002.0      Platform       Kemco      0.01      0.00      0.00   
16594  2003.0       Shooter  Infogrames      0.01      0.00      0.00   
16595  2008.0        Racing  Activision      0.00      0.00      0.00   
16596  2010.0        Puzzle    7G//AMES      0.00      0.01      0.00   
16597  2003.0      Platform     Wanadoo      0.01      0.00      0.00   

       Other_Sales  Global_Sales  
0             8.46         82.74  
1             0.77         40.24  
2             3.31         35.82  
3             2.96         33.00  
4             1.00         31.37  
...            ...           ...  
16593         0.00          0.01  
16594         0.00          0.01  
16595         0.00          0.01  
16596         0.00          0.01  
16597         0.00          0.01  

[16598 rows x 11 columns]

In [8]:
# Visualizando os dados com yprofile
from ydata_profiling import ProfileReport
profile = ProfileReport(df, title="Profiling Report")
profile

/opt/conda/lib/python3.11/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
/opt/conda/lib/python3.11/site-packages/visions/backends/shared/nan_handling.py:50: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @nb.jit


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Limpeza dos dados

A partir desse ponto vamos iniciar o processo de limpeza dos dados

In [21]:
# Pegando os nomes das colunas
df.columns

Index(['Rank', 'Name', 'Platform', 'Year', 'Genre', 'Publisher', 'NA_Sales',
       'EU_Sales', 'JP_Sales', 'Other_Sales', 'Global_Sales'],
      dtype='object')

In [29]:
# Removendo as colunas com alta correlação
df = df.drop(columns=['Rank', 'NA_Sales', 'EU_Sales', 'JP_Sales', 'Other_Sales', 'Name', 'Publisher'])

In [23]:
# Pegando os valores encodados
pd.get_dummies(df)

Year  Global_Sales  Platform_2600  Platform_3DO  Platform_3DS  \
0      2006.0         82.74          False         False         False   
1      1985.0         40.24          False         False         False   
2      2008.0         35.82          False         False         False   
3      2009.0         33.00          False         False         False   
4      1996.0         31.37          False         False         False   
...       ...           ...            ...           ...           ...   
16593  2002.0          0.01          False         False         False   
16594  2003.0          0.01          False         False         False   
16595  2008.0          0.01          False         False         False   
16596  2010.0          0.01          False         False         False   
16597  2003.0          0.01          False         False         False   

       Platform_DC  Platform_DS  Platform_GB  Platform_GBA  Platform_GC  ...  \
0            False        False        False         False        False  ...   
1            False        False        False         False        False  ...   
2            False        False        False         False        False  ...   
3            False        False        False         False        False  ...   
4            False        False         True         False        False  ...   
...            ...          ...          ...           ...          ...  ...   
16593        False        False        False          True        False  ...   
16594        False        False        False         False         True  ...   
16595        False        False        False         False        False  ...   
16596        False         True        False         False        False  ...   
16597        False        False        False          True        False  ...   

       Genre_Fighting  Genre_Misc  Genre_Platform  Genre_Puzzle  Genre_Racing  \
0               False       False           False         False         False   
1               False       False            True         False         False   
2               False       False           False         False          True   
3               False       False           False         False         False   
4               False       False           False         False         False   
...               ...         ...             ...           ...           ...   
16593           False       False            True         False         False   
16594           False       False           False         False         False   
16595           False       False           False         False          True   
16596           False       False           False          True         False   
16597           False       False            True         False         False   

       Genre_Role-Playing  Genre_Shooter  Genre_Simulation  Genre_Sports  \
0                   False          False             False          True   
1                   False          False             False         False   
2                   False          False             False         False   
3                   False          False             False          True   
4                    True          False             False         False   
...                   ...            ...               ...           ...   
16593               False          False             False         False   
16594               False           True             False         False   
16595               False          False             False         False   
16596               False          False             False         False   
16597               False          False             False         False   

       Genre_Strategy  
0               False  
1               False  
2               False  
3               False  
4               False  
...               ...  
16593           False  
16594           False  
16595           False  
16596           False  
16597    

## Alternativa: utilizar o OneHotEncoding

Sempre gera o mesmo padrão de transformação de dados. Assim se os dados de entrada não possuirem os mesmos dados que o conjunto de treinamento não possua todos os mesmos parâmetros.

- [Preprocessing: OneHotEncoder() vs pandas.get_dummies](https://albertum.medium.com/preprocessing-onehotencoder-vs-pandas-get-dummies-3de1f3d77dcc#:~:text=In%20short%2C%20if%20I'm,processing%20on%20my%20test%20set.)
- [get_dummies vs OneHotEncoder: qual método escolher?](https://www.alura.com.br/artigos/get-dummies-vs-onehotencoder-qual-metodo-escolher)

In [40]:
from sklearn.compose import make_column_transformer
from sklearn.preprocessing import OneHotEncoder

colunas_categoricas = ['Platform', 'Genre']

one_hot_enc = make_column_transformer(
    (
        OneHotEncoder(
            categories='auto',  # Categories per feature
            drop=None, # Whether to drop one of the features
            sparse=False, # Will return sparse matrix if set True
            handle_unknown = 'ignore'
        ),
        colunas_categoricas
    ),
    remainder='passthrough')


In [42]:
tranformed = one_hot_enc.fit_transform(df)
tranformed_df = pd.DataFrame(tranformed, columns=one_hot_enc.get_feature_names_out())
tranformed_df

/opt/conda/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:972: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


onehotencoder__Platform_2600  onehotencoder__Platform_3DO  \
0                               0.0                          0.0   
1                               0.0                          0.0   
2                               0.0                          0.0   
3                               0.0                          0.0   
4                               0.0                          0.0   
...                             ...                          ...   
16593                           0.0                          0.0   
16594                           0.0                          0.0   
16595                           0.0                          0.0   
16596                           0.0                          0.0   
16597                           0.0                          0.0   

       onehotencoder__Platform_3DS  onehotencoder__Platform_DC  \
0                              0.0                         0.0   
1                              0.0                         0.0   
2                              0.0                         0.0   
3                              0.0                         0.0   
4                              0.0                         0.0   
...                            ...                         ...   
16593                          0.0                         0.0   
16594                          0.0                         0.0   
16595                          0.0                         0.0   
16596                          0.0                         0.0   
16597                          0.0                         0.0   

       onehotencoder__Platform_DS  onehotencoder__Platform_GB  \
0                             0.0                         0.0   
1                             0.0                         0.0   
2                             0.0                         0.0   
3                             0.0                         0.0   
4                             0.0                         1.0   
...                           ...                         ...   
16593                         0.0                         0.0   
16594                         0.0                         0.0   
16595                         0.0                         0.0   
16596                         1.0                         0.0   
16597                         0.0                         0.0   

       onehotencoder__Platform_GBA  onehotencoder__Platform_GC  \
0                              0.0                         0.0   
1                              0.0                         0.0   
2                              0.0                         0.0   
3                              0.0                         0.0   
4                              0.0                         0.0   
...                            ...                         ...   
16593                          1.0                         0.0   
16594                          0.0                         1.0   
16595                          0.0                         0.0   
16596                          0.0                         0.0   
16597                          1.0                         0.0   

       onehotencoder__Platform_GEN  onehotencoder__Platform_GG  ...  \
0                              0.0                         0.0  ...   
1                              0.0                         0.0  ...   
2                              0.0                         0.0  ...   
3                              0.0                         0.0  ...   
4                              0.0                         0.0  ...   
...                            ...                         ...  ...   
16593                          0.0                         0.0  ...   
16594                          0.0                         0.0  ...   
16595                          0.0                         0.0  ...   
16596                          0.0                         0.0  ...   
16597                          0.0        

In [43]:
# Agora vamos normalizar os dados do ano
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
scaled = scaler.fit_transform(tranformed_df)

In [54]:
# convert the array back to a dataframe
dataset_scaled = pd.DataFrame(scaled, columns=[tranformed_df.columns])
dataset_scaled

onehotencoder__Platform_2600 onehotencoder__Platform_3DO  \
0                              0.0                         0.0   
1                              0.0                         0.0   
2                              0.0                         0.0   
3                              0.0                         0.0   
4                              0.0                         0.0   
...                            ...                         ...   
16593                          0.0                         0.0   
16594                          0.0                         0.0   
16595                          0.0                         0.0   
16596                          0.0                         0.0   
16597                          0.0                         0.0   

      onehotencoder__Platform_3DS onehotencoder__Platform_DC  \
0                             0.0                        0.0   
1                             0.0                        0.0   
2                             0.0                        0.0   
3                             0.0                        0.0   
4                             0.0                        0.0   
...                           ...                        ...   
16593                         0.0                        0.0   
16594                         0.0                        0.0   
16595                         0.0                        0.0   
16596                         0.0                        0.0   
16597                         0.0                        0.0   

      onehotencoder__Platform_DS onehotencoder__Platform_GB  \
0                            0.0                        0.0   
1                            0.0                        0.0   
2                            0.0                        0.0   
3                            0.0                        0.0   
4                            0.0                        1.0   
...                          ...                        ...   
16593                        0.0                        0.0   
16594                        0.0                        0.0   
16595                        0.0                        0.0   
16596                        1.0                        0.0   
16597                        0.0                        0.0   

      onehotencoder__Platform_GBA onehotencoder__Platform_GC  \
0                             0.0                        0.0   
1                             0.0                        0.0   
2                             0.0                        0.0   
3                             0.0                        0.0   
4                             0.0                        0.0   
...                           ...                        ...   
16593                         1.0                        0.0   
16594                         0.0                        1.0   
16595                         0.0                        0.0   
16596                         0.0                        0.0   
16597                         1.0                        0.0   

      onehotencoder__Platform_GEN onehotencoder__Platform_GG  ...  \
0                             0.0                        0.0  ...   
1                             0.0                        0.0  ...   
2                             0.0                        0.0  ...   
3                             0.0                        0.0  ...   
4                             0.0                        0.0  ...   
...                           ...                        ...  ...   
16593                         0.0                        0.0  ...   
16594                         0.0                        0.0  ...   
16595                         0.0                        0.0  ...   
16596                         0.0                        0.0  ...   
16597                         0.0                        0.0  ...   

      onehotencoder__Genre_Platform onehotencoder__Genre_Puzzle  \
0                     

In [55]:
# Retirando dados nulos
data = dataset_scaled.dropna(axis=1)

In [56]:
data

onehotencoder__Platform_2600 onehotencoder__Platform_3DO  \
0                              0.0                         0.0   
1                              0.0                         0.0   
2                              0.0                         0.0   
3                              0.0                         0.0   
4                              0.0                         0.0   
...                            ...                         ...   
16593                          0.0                         0.0   
16594                          0.0                         0.0   
16595                          0.0                         0.0   
16596                          0.0                         0.0   
16597                          0.0                         0.0   

      onehotencoder__Platform_3DS onehotencoder__Platform_DC  \
0                             0.0                        0.0   
1                             0.0                        0.0   
2                             0.0                        0.0   
3                             0.0                        0.0   
4                             0.0                        0.0   
...                           ...                        ...   
16593                         0.0                        0.0   
16594                         0.0                        0.0   
16595                         0.0                        0.0   
16596                         0.0                        0.0   
16597                         0.0                        0.0   

      onehotencoder__Platform_DS onehotencoder__Platform_GB  \
0                            0.0                        0.0   
1                            0.0                        0.0   
2                            0.0                        0.0   
3                            0.0                        0.0   
4                            0.0                        1.0   
...                          ...                        ...   
16593                        0.0                        0.0   
16594                        0.0                        0.0   
16595                        0.0                        0.0   
16596                        1.0                        0.0   
16597                        0.0                        0.0   

      onehotencoder__Platform_GBA onehotencoder__Platform_GC  \
0                             0.0                        0.0   
1                             0.0                        0.0   
2                             0.0                        0.0   
3                             0.0                        0.0   
4                             0.0                        0.0   
...                           ...                        ...   
16593                         1.0                        0.0   
16594                         0.0                        1.0   
16595                         0.0                        0.0   
16596                         0.0                        0.0   
16597                         1.0                        0.0   

      onehotencoder__Platform_GEN onehotencoder__Platform_GG  ...  \
0                             0.0                        0.0  ...   
1                             0.0                        0.0  ...   
2                             0.0                        0.0  ...   
3                             0.0                        0.0  ...   
4                             0.0                        0.0  ...   
...                           ...                        ...  ...   
16593                         0.0                        0.0  ...   
16594                         0.0                        0.0  ...   
16595                         0.0                        0.0  ...   
16596                         0.0                        0.0  ...   
16597                         0.0                        0.0  ...   

      onehotencoder__Genre_Misc onehotencoder__Genre_Platform  \
0                       

# Treinando o Modelo

Agora vamos treinar um modelo de regressão linear simples.

In [57]:
# Primeiro dividimos os dados de treino e os dados de teste
y = data.pop('remainder__Global_Sales')
X = data
X_train, X_test, y_train, y_test = train_test_split(
    X,y, test_size=0.3, random_state=42
)

In [58]:
# Modelo de regressão linear
from sklearn.linear_model import LinearRegression
modelo = LinearRegression().fit(X_train, y_train)

In [60]:
modelo.score(X_test, y_test)

-1.2301830789125806e+21